In [12]:
import pandas as pd
import torch
import numpy as np
from machine_learning import nn, preprocessing as pp
import requests
import io
import cufflinks as cf
cf.go_offline()
import logging 
from toolz import pipe

logger = logging.getLogger(__name__)
logging.basicConfig()
logger.setLevel(logging.INFO)

In [4]:
%load_ext autoreload
%autoreload 2


In [13]:
breast_cancer = pd.read_csv(
    io.BytesIO(requests.get(
        "https://archive.ics.uci.edu/ml/machine-learning-databases/breast-cancer-wisconsin/breast-cancer-wisconsin.data",
        verify=False
    ).content),
    header=None, 
    names=[
        "id_number", 
        "clump_thickness", 
        'uniformity_cell_size', 
        'uniformity_cell_shape', 
        "marginal_adhesion",
        "single_epithelial_cell_size", 
        "bare_nuclei", 
        "bland_chromatin", "normal_nucleoli", "mitosis", "class"
    ]
).replace('?',np.NaN).astype('float', errors='ignore').dropna()


/Users/home/miniconda3/lib/python3.7/site-packages/urllib3/connectionpool.py:1004: InsecureRequestWarning:

Unverified HTTPS request is being made to host 'archive.ics.uci.edu'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings



In [23]:
from machine_learning import validation
from scipy import stats

def score_func(y, yhat):
    return np.mean(np.argmax(y, axis=1) == yhat)

def run_classification_experiment(
    X, 
    y, 
    learning_rate_choices=np.linspace(.001, .01, 10), 
    hidden_layer_choices=list(range(3, 16, 3)),
    n_iter=10000, 
    conv_tol=.001
):
    kfold = validation.KFoldStratifiedCV(num_folds=5)
    accuracy_0h = []
    accuracy_1h = []
    accuracy_2h = []
    baseline = []

    split = 0 
    for train, test in kfold.split(X=X, y=y.reshape(-1, )):
        split += 1
        logger.info(f"CV Iteration: {split}")
        logger.info("Standardizing data")
        max_scaler = pp.Standardizer()
        X_train = max_scaler.fit_transform(X[train])
        X_test = max_scaler.transform(X[test])        
        y_train = pd.get_dummies(y[train]).values
        
        if split == 1:
            logger.info("Finding learning rate for H0")
            h0_callable = lambda lr: nn.SequentialNetwork(
                nn.LinearSigmoid(in_features=X_train.shape[1], out_features=y_train.shape[1]),
                convergence_tol=conv_tol,
                n_iter=n_iter,
                learning_rate=lr,
                batch_size=48
            )

            results = list(validation.GridSearchCV(
                model_callable=h0_callable, 
                param_grid={"lr": learning_rate_choices}, 
                scoring_func=score_func,
                cv_object=validation.KFoldCV(num_folds=3)
            ).get_cv_scores(X=X_train, y=y_train))
            
            best_model_h0 = h0_callable(**sorted(results, key=lambda x: x[-1], reverse=True)[0][0])
            logger.info(f"Results: {sorted(results, key=lambda x: x[-1], reverse=True)[0][0]}")

            logger.info("Finding topology and learning rate for H1")
            h1_callable = lambda h1, lr: nn.SequentialNetwork(
                nn.LinearSigmoid(in_features=X_train.shape[1], out_features=h1, bias=True),
                nn.LinearSigmoid(in_features=h1, out_features=y_train.shape[1], bias=True),
                convergence_tol=conv_tol,
                n_iter=n_iter,
                learning_rate=lr,
                batch_size=X_train.shape[1]
            )

            results = list(validation.GridSearchCV(
                model_callable=h1_callable, 
                param_grid={'h1': hidden_layer_choices, "lr": learning_rate_choices}, 
                scoring_func=score_func, 
                cv_object=validation.KFoldCV(num_folds=3)
            ).get_cv_scores(X=X_train, y=y_train))

            best_model_h1 = h1_callable(**sorted(results, key=lambda x: x[-1], reverse=True)[0][0])
            logger.info(f"Results: {sorted(results, key=lambda x: x[-1], reverse=True)[0][0]}")
            
            logger.info("Finding topology and learning rate for H2")
            h2_callable = lambda h1, h2, lr: nn.SequentialNetwork(
                nn.LinearSigmoid(in_features=X_train.shape[1], out_features=h1, bias=True),
                nn.LinearSigmoid(in_features=h1, out_features=h2, bias=True),
                nn.LinearSigmoid(in_features=h2, out_features=y_train.shape[1], bias=True),
                convergence_tol=conv_tol,
                n_iter=n_iter,
                learning_rate=lr,
                batch_size=X_train.shape[1]
            )

            results = list(validation.GridSearchCV(
                model_callable=h2_callable, 
                param_grid={'h1': hidden_layer_choices, 'h2': hidden_layer_choices,  "lr": learning_rate_choices}, 
                scoring_func=score_func, 
                cv_object=validation.KFoldCV(num_folds=3)
            ).get_cv_scores(X=X_train, y=y_train))
            logger.info(f"Results: {sorted(results, key=lambda x: x[-1], reverse=True)[0][0]}")
            best_model_h2 = h2_callable(**sorted(results, key=lambda x: x[-1], reverse=True)[0][0])

        best_model_h0.fit(X_train, y_train)
        best_model_h1.fit(X_train, y_train)
        best_model_h2.fit(X_train, y_train)

        baseline.append(np.mean(stats.mode(y[train]).mode[0]  == y[test]))
        accuracy_0h.append(np.mean(best_model_h0.predict(X_test) == y[test]))
        accuracy_1h.append(np.mean(best_model_h1.predict(X_test) == y[test]))
        accuracy_2h.append(np.mean(best_model_h2.predict(X_test) == y[test]))
    return {
        "models": {
            'h0': best_model_h0, 
            'h1': best_model_h1, 
            'h2': best_model_h2, 
        }, 
        'accuracy': {
            'h0': accuracy_0h, 
            'h1': accuracy_1h, 
            'h2': accuracy_2h, 
            'baseline': baseline
        }
    }

In [24]:
X, y = (
    breast_cancer.drop(['id_number', 'class'], axis=1).values,
    breast_cancer['class'].astype('category').cat.codes.values.reshape(-1, )
)
np.random.seed(73)
breast_cancer_results = run_classification_experiment(X=X, y=y)

INFO:__main__:CV Iteration: 1
INFO:__main__:Standardizing data
INFO:__main__:Finding learning rate for H0


Gradient update: 
[[  1.47722694  -1.47722694]
 [ -7.98385008   7.98385008]
 [ -9.00724794   9.00724794]
 [ -9.23622641   9.23622641]
 [ -7.89400871   7.89400871]
 [ -8.20014306   8.20014306]
 [-10.34840674  10.34840674]
 [-10.05999129  10.05999129]
 [ -6.89301301   6.89301301]
 [ -2.90823357   2.90823357]]
Gradient update: 
[[ 5.45940364 -5.45940364]
 [-8.45091448  8.45091448]
 [-9.18116634  9.18116634]
 [-9.30213288  9.30213288]
 [-6.95375003  6.95375003]
 [-8.82089545  8.82089545]
 [-7.80657318  7.80657318]
 [-7.74344768  7.74344768]
 [-8.07568701  8.07568701]
 [-3.39931155  3.39931155]]
Gradient update: 
[[  4.44500246  -4.44500246]
 [ -8.2538632    8.2538632 ]
 [-10.17546964  10.17546964]
 [ -9.96232625   9.96232625]
 [ -6.29712213   6.29712213]
 [ -7.03484493   7.03484493]
 [ -8.02807627   8.02807627]
 [ -9.55327908   9.55327908]
 [ -9.44232359   9.44232359]
 [ -3.70351281   3.70351281]]
Gradient update: 
[[ 3.68797918 -3.68797918]
 [-2.44139018  2.44139018]
 [-2.88533668  2.8853

Gradient update: 
[[ 3.47647081 -3.47647081]
 [-4.15662279  4.15662279]
 [-3.58230002  3.58230002]
 [-3.35329577  3.35329577]
 [-1.54888709  1.54888709]
 [-1.55176579  1.55176579]
 [-3.3487237   3.3487237 ]
 [-3.59939747  3.59939747]
 [-2.58843504  2.58843504]
 [-2.20240535  2.20240535]]
Gradient update: 
[[ 2.93132432 -2.93132432]
 [-2.70948455  2.70948455]
 [-3.89832543  3.89832543]
 [-3.59256905  3.59256905]
 [-3.47498953  3.47498953]
 [-2.53969684  2.53969684]
 [-4.2589643   4.2589643 ]
 [-4.21240311  4.21240311]
 [-3.14638281  3.14638281]
 [-2.25025412  2.25025412]]
Gradient update: 
[[ 3.11303982 -3.11303982]
 [-3.13428291  3.13428291]
 [-3.37794208  3.37794208]
 [-3.15345993  3.15345993]
 [-3.3092831   3.3092831 ]
 [-2.35112673  2.35112673]
 [-3.94678292  3.94678292]
 [-3.99532911  3.99532911]
 [-3.61732492  3.61732492]
 [-0.60227043  0.60227043]]
Gradient update: 
[[ 1.45076572 -1.45076572]
 [-2.15848299  2.15848299]
 [-3.01019763  3.01019763]
 [-3.36635908  3.36635908]
 [-4.49

Gradient update: 
[[ 1.90357534 -1.90357534]
 [-3.33417791  3.33417791]
 [-3.70590739  3.70590739]
 [-3.63364297  3.63364297]
 [-3.9976983   3.9976983 ]
 [-3.44197193  3.44197193]
 [-4.09816832  4.09816832]
 [-3.98079012  3.98079012]
 [-2.91825525  2.91825525]
 [-1.77764123  1.77764123]]
Gradient update: 
[[ 1.26905023 -1.26905023]
 [-3.80295657  3.80295657]
 [-3.88536564  3.88536564]
 [-3.76034118  3.76034118]
 [-3.4081536   3.4081536 ]
 [-2.9045223   2.9045223 ]
 [-3.42295279  3.42295279]
 [-3.38335212  3.38335212]
 [-2.94654823  2.94654823]
 [-3.21038948  3.21038948]]
Gradient update: 
[[ 1.08733473 -1.08733473]
 [-4.45862975  4.45862975]
 [-4.34111419  4.34111419]
 [-4.46574546  4.46574546]
 [-3.35257704  3.35257704]
 [-3.15190989  3.15190989]
 [-3.57643844  3.57643844]
 [-4.11888288  4.11888288]
 [-3.65748449  3.65748449]
 [-2.05264486  2.05264486]]
Gradient update: 
[[ 4.49652674 -4.49652674]
 [-8.9740663   8.9740663 ]
 [-8.70707425  8.70707425]
 [-8.87018858  8.87018858]
 [-5.73

INFO:__main__:Results: {'lr': 0.001}
INFO:__main__:Finding topology and learning rate for H1


...

Gradient update: 
[[ 2.74960882 -2.74960882]
 [-4.22468329  4.22468329]
 [-3.95904055  3.95904055]
 [-3.95565904  3.95565904]
 [-3.92715549  3.92715549]
 [-3.40458807  3.40458807]
 [-4.05454379  4.05454379]
 [-3.95862413  3.95862413]
 [-3.02205183  3.02205183]
 [-1.93199366  1.93199366]]
Gradient update: 
[[ 1.4805586  -1.4805586 ]
 [-3.56894915  3.56894915]
 [-3.74607442  3.74607442]
 [-3.79551897  3.79551897]
 [-2.68653043  2.68653043]
 [-2.48522107  2.48522107]
 [-4.10032332  4.10032332]
 [-3.07400786  3.07400786]
 [-2.98501703  2.98501703]
 [-1.75310535  1.75310535]]
Gradient update: 
[[ 2.11508371 -2.11508371]
 [-3.2269331   3.2269331 ]
 [-3.72955236  3.72955236]
 [-3.53899795  3.53899795]
 [-2.67274323  2.67274323]
 [-3.05878059  3.05878059]
 [-3.53768295  3.53768295]
 [-3.1232104   3.1232104 ]
 [-1.91025118  1.91025118]
 [-1.17146817  1.17146817]]
Gradient update: 
[[ 0.63656856 -0.63656856]
 [ 0.84603319 -0.84603319]
 [ 0.84603318 -0.84603318]
 [ 0.84603318 -0.84603318]]
Gradie

INFO:__main__:CV Iteration: 4
INFO:__main__:Standardizing data


Gradient update: 
[[ 1.08733473 -1.08733473]
 [-4.34228406  4.34228406]
 [-3.67236328  3.67236328]
 [-3.45096395  3.45096395]
 [-3.65303393  3.65303393]
 [-3.23694896  3.23694896]
 [-4.05289641  4.05289641]
 [-3.29103688  3.29103688]
 [-3.4812586   3.4812586 ]
 [-2.17064455  2.17064455]]
Gradient update: 
[[ 0.45280962 -0.45280962]
 [-2.70035434  2.70035434]
 [-4.46957551  4.46957551]
 [-4.25051071  4.25051071]
 [-3.9296903   3.9296903 ]
 [-3.36446545  3.36446545]
 [-5.03146965  5.03146965]
 [-4.30463052  4.30463052]
 [-3.48584337  3.48584337]
 [-1.6334437   1.6334437 ]]
Gradient update: 
[[ 1.69206697 -1.69206697]
 [-3.79267311  3.79267311]
 [-4.77013807  4.77013807]
 [-5.28961097  5.28961097]
 [-3.29953103  3.29953103]
 [-3.86290787  3.86290787]
 [-4.24003254  4.24003254]
 [-3.49522696  3.49522696]
 [-3.94724831  3.94724831]
 [-3.06408431  3.06408431]]
Gradient update: 
[[ 0.63426066 -0.63426066]
 [ 0.84603342 -0.84603342]
 [ 0.84603342 -0.84603342]
 [ 0.84603342 -0.84603342]]
Gradie

INFO:__main__:CV Iteration: 5
INFO:__main__:Standardizing data


Gradient update: 
[[ 3.11303982 -3.11303982]
 [-2.85739092  2.85739092]
 [-3.25050909  3.25050909]
 [-3.25839967  3.25839967]
 [-2.47335677  2.47335677]
 [-3.24639948  3.24639948]
 [-3.82088208  3.82088208]
 [-3.05864732  3.05864732]
 [-3.14943792  3.14943792]
 [-3.13174496  3.13174496]]
Gradient update: 
[[ 0.66431799 -0.66431799]
 [-3.86506076  3.86506076]
 [-3.2777507   3.2777507 ]
 [-3.49801352  3.49801352]
 [-3.15883104  3.15883104]
 [-3.25035155  3.25035155]
 [-3.68571019  3.68571019]
 [-3.10014933  3.10014933]
 [-2.50687537  2.50687537]
 [-1.79284187  1.79284187]]
Gradient update: 
[[ 0.93541211 -0.93541211]
 [-3.48585873  3.48585873]
 [-4.4401181   4.4401181 ]
 [-4.37060909  4.37060909]
 [-3.86076564  3.86076564]
 [-3.46544732  3.46544732]
 [-4.11480188  4.11480188]
 [-3.57503401  3.57503401]
 [-3.83931912  3.83931912]
 [-1.96945042  1.96945042]]
Gradient update: 
[[ 0.73056292 -0.73056292]
 [ 0.52877093 -0.52877093]
 [ 0.52877093 -0.52877093]
 [ 0.52877093 -0.52877093]]
Gradie

In [20]:
np.random.seed(73)
logger.info("Iris Experiment")
iris_data = pd.read_csv(
    "https://archive.ics.uci.edu/ml/machine-learning-databases/iris/iris.data",
    header=None,
    names=["sepal_length", "sepal_width", "petal_length", "petal_width", "class"],
)

X, y = (
    iris_data.drop(["class"], axis=1).values,
    iris_data["class"].astype("category").cat.codes.values,
)
iris_results = run_classification_experiment(
    X=X,
    y=y,
    learning_rate_choices=list(np.linspace(0.01, 0.8, 5)),
    hidden_layer_choices=[3, 4],
    n_iter=500,
    conv_tol=0.001
)

logger.info(f"Iris Results: {dicttoolz.valmap(np.mean, iris_results['accuracy'])}")


INFO:__main__:Iris Experiment
INFO:__main__:CV Iteration: 1
INFO:__main__:Standardizing data
INFO:__main__:Finding learning rate for H0


Gradient update: 
[[-0.45376191  0.89314241 -0.45275192]
 [-6.68854516  1.75577859  4.92405483]
 [ 4.07789778 -5.92345744  1.83853234]
 [-8.37726495  1.9601228   6.40712188]
 [-8.46961053  0.39135183  8.0653334 ]]
Gradient update: 
[[-3.61663347  1.30970104  2.72330276]
 [-6.29296337 -1.54904131  8.04540178]
 [ 2.49890248 -5.26135994  2.80409762]
 [-6.74365943 -0.6864152   7.57836712]
 [-6.4087637  -2.08978752  8.65214932]]
Gradient update: 
[[-1.50450071 -1.71174399  4.11352495]
 [-7.09126302 -0.94877076  8.41811494]
 [ 4.29960224 -2.97936473 -0.9571892 ]
 [-7.62572161 -0.83130378  8.72527692]
 [-7.63922393 -1.65940398  9.58568664]]
Gradient update: 
[[ 3.55709791 -0.41353406 -0.61228004]
 [-5.25896271  1.65910574  2.78005287]
 [ 6.13942234 -4.32264171 -0.47746272]
 [-7.2073847   1.9942224   3.91081144]
 [-7.21584906  1.26150156  4.82930679]]
Gradient update: 
[[ 0.61115528  2.47625238 -1.15357056]
 [-3.26195039  0.50160287  2.36692049]
 [ 4.2822318  -3.66407686 -0.24136823]
 [-4.9126

/Users/home/Documents/JHU/machine_learning/machine_learning/nn.py:15: RuntimeWarning:

overflow encountered in exp



Gradient update: 
[[ 0.90148725  1.31555491 -0.64314899]
 [-4.11461973  0.31353171  3.34248813]
 [ 2.73070086 -1.94998688 -0.77725574]
 [-4.76210858  0.45091202  3.86133319]
 [-4.49187186 -0.1177803   4.11268033]]
Gradient update: 
[[-0.55254434  2.33469608 -0.36952942]
 [-2.74367299 -0.96332714  3.83262756]
 [ 3.38981869 -2.48662181 -0.63230323]
 [-3.94066534 -0.17644019  3.99845023]
 [-3.92804174 -0.17964126  3.99568807]]
Gradient update: 
[[ 2.44046377  0.57660749 -0.85846236]
 [-5.25569079  0.74402529  3.6770019 ]
 [ 3.68635308 -2.90474349  0.16164133]
 [-6.38611572  1.38488733  4.07082736]
 [-6.33725802  0.90809362  4.6989988 ]]
Gradient update: 
[[  1.33547534  -0.02202993  -1.31746444]
 [ -8.54625244   2.63933678   5.91544291]
 [  6.05867165  -3.90611187  -2.15972539]
 [-10.20119349   3.00840048   7.20209863]
 [ -9.26075999   2.37994353   6.88869268]]
Gradient update: 
[[-0.36240147  4.04207462 -1.92466082]
 [-2.89796894 -0.75623852  3.53975754]
 [ 2.02539063 -3.84775476  1.5830

INFO:__main__:Results: {'lr': 0.01}
INFO:__main__:Finding topology and learning rate for H1


TypeError: __init__() got an unexpected keyword argument 'fit_intercept'

In [16]:
from toolz import pipe

# Next, we repeat this process on the Soybean data
soybean_data = pipe(
    pd.read_csv(
         io.BytesIO(requests.get(
                "https://archive.ics.uci.edu/ml/machine-learning-databases/soybean/soybean-small.data",
        verify=False
        ).content),
        header=None,
        names=[
            "date",
            "plant-stand",
            "precip",
            "temp",
            "hail",
            "crop-hist",
            "area-damaged",
            "severity",
            "seed-tmt",
            "germination",
            "plant-growth",
            "leaves",
            "leafspots-halo",
            "leafspots-marg",
            "leafspot-size",
            "leaf-shread",
            "leaf-malf",
            "leaf-mild",
            "stem",
            "lodging",
            "stem-cankers",
            "canker-lesion",
            "fruiting-bodies",
            "external decay",
            "mycelium",
            "int-discolor",
            "sclerotia",
            "fruit-pods",
            "fruit spots",
            "seed",
            "mold-growth",
            "seed-discolor",
            "seed-size",
            "shriveling",
            "roots",
            "instance_class",
        ],
    )
    .pipe(lambda df: df.loc(axis=1)[df.nunique() > 1])  # drop columns with no variance
    .assign(instance_class=lambda df: df["instance_class"].astype("category").cat.codes)
)

X, y = (
    pd.get_dummies(
        soybean_data.drop('instance_class', axis=1),
        columns=soybean_data.drop('instance_class', axis=1).columns, 
        drop_first=True
    ).values, 
    soybean_data['instance_class'].values
)


soybean_results = run_classification_experiment(
    X, 
    y=y, 
    learning_rate_choices=np.linspace(.00001, .0001, 5), 
    hidden_layer_choices=list(range(5, 11, 2)), 
)

/Users/home/miniconda3/lib/python3.7/site-packages/urllib3/connectionpool.py:1004: InsecureRequestWarning:

Unverified HTTPS request is being made to host 'archive.ics.uci.edu'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings

INFO:__main__:CV Iteration: 1
INFO:__main__:Standardizing data
INFO:__main__:Finding learning rate for H0


ValueError: operands could not be broadcast together with shapes (48,4) (48,) 

In [67]:
soybean_results

{'models': {'h0': <machine_learning.nn.SequentialNetwork at 0x130fe2610>,
  'h1': <machine_learning.nn.SequentialNetwork at 0x131b5fc10>,
  'h2': <machine_learning.nn.SequentialNetwork at 0x130e8b410>},
 'accuracy': {'h0': [0.6666666666666666, 1.0, 1.0, 1.0, 1.0],
  'h1': [0.2222222222222222, 0.3333333333333333, 0.3333333333333333, 0.4, 0.4],
  'h2': [0.3333333333333333, 0.3333333333333333, 0.3333333333333333, 0.4, 0.4],
  'baseline': [0.3333333333333333,
   0.3333333333333333,
   0.3333333333333333,
   0.4,
   0.4]}}

In [60]:
pd.Series(soybean_results['models']['h2'].loss).rolling(10).mean().iplot()

In [128]:
iris_data = pd.read_csv(
    "https://archive.ics.uci.edu/ml/machine-learning-databases/iris/iris.data", 
    header=None, names=['sepal_length', 'sepal_width', 'petal_length', 'petal_width', 'class']
)

X, y = (
    iris_data.drop(['class'], axis=1).values, 
    iris_data['class'].astype('category').cat.codes.values
)

In [136]:
iris_results = run_classification_experiment(
    X=X, 
    y=y, 
    learning_rate_choices=list(np.linspace(.001, 1,  10)), 
    hidden_layer_choices=[4], 
    n_iter=15000, 
    conv_tol=.01
)

INFO:__main__:CV Iteration: 1
INFO:__main__:Standardizing data
INFO:__main__:Finding learning rate for H0
INFO:__main__:Results: {'lr': 0.001}
INFO:__main__:Finding topology and learning rate for H1
INFO:__main__:Results: {'h1': 4, 'lr': 0.778}
INFO:__main__:Finding topology and learning rate for H2
INFO:__main__:Results: {'h1': 4, 'h2': 4, 'lr': 0.334}
INFO:__main__:CV Iteration: 2
INFO:__main__:Standardizing data
INFO:__main__:CV Iteration: 3
INFO:__main__:Standardizing data
INFO:__main__:CV Iteration: 4
INFO:__main__:Standardizing data
INFO:__main__:CV Iteration: 5
INFO:__main__:Standardizing data


In [137]:
iris_results

{'models': {'h0': <machine_learning.nn.SequentialNetwork at 0x132067810>,
  'h1': <machine_learning.nn.SequentialNetwork at 0x1324ff150>,
  'h2': <machine_learning.nn.SequentialNetwork at 0x131e1bed0>},
 'accuracy': {'h0': [0.7333333333333333,
   0.8666666666666667,
   0.8333333333333334,
   0.6333333333333333,
   0.6333333333333333],
  'h1': [0.9,
   0.6666666666666666,
   0.6666666666666666,
   0.6666666666666666,
   0.6666666666666666],
  'h2': [0.6666666666666666,
   0.6666666666666666,
   0.3333333333333333,
   0.3333333333333333,
   0.3333333333333333],
  'baseline': [0.3333333333333333,
   0.3333333333333333,
   0.3333333333333333,
   0.3333333333333333,
   0.3333333333333333]}}

In [11]:
house_votes_data = pipe(
    pd.read_csv(
        "https://archive.ics.uci.edu/ml/machine-learning-databases/voting-records/house-votes-84.data",
        header=None,
        names=[
            "instance_class",
            "handicapped-infants",
            "water-project-cost-sharing",
            "adoption-of-the-budget-resolution",
            "physician-fee-freeze",
            "el-salvador-aid",
            "religious-groups-in-schools",
            "anti-satellite-test-ban",
            "aid-to-nicaraguan-contras",
            "mx-missile",
            "immigration",
            "synfuels-corporation-cutback",
            "education-spending",
            "superfund-right-to-sue",
            "crime",
            "duty-free-exports",
            "export-administration-act-south-africa",
        ],
    )
    .replace("?", np.NaN)
    .replace("y", 1)
    .replace("n", 0), 
    lambda df: pd.get_dummies(df, columns=df.columns, drop_first=True, dummy_na=True)
)

X, y = (
    house_votes_data.drop(['instance_class_republican', 'instance_class_nan'], axis=1).values, 
    house_votes_data['instance_class_republican'].values
)


run_classification_experiment(
    X=X, 
    y=y,     
    learning_rate_choices=list(np.linspace(.001, 1,  10)), 
    hidden_layer_choices=[4], 
    n_iter=1500, 
    conv_tol=.01
)

INFO:__main__:CV Iteration: 1
INFO:__main__:Standardizing data
INFO:__main__:Finding learning rate for H0


ValueError: operands could not be broadcast together with shapes (48,2) (48,) 